In [1]:
!pip install --upgrade setuptools
!pip install lxml
!pip install geocoder
!pip install folium
!pip install area
!pip install geojson
!pip install pyproj
!pip install shapely


import io
import pandas as pd # library for data analsysis
import numpy as np # library to handle data in a vectorized manner
import geocoder 
import folium # map rendering library
import json # library to handle JSON files
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe
from area import area
import geojson
from shapely.geometry import Polygon
from shapely.ops import transform
import pyproj


Requirement already up-to-date: setuptools in /opt/conda/envs/Python36/lib/python3.6/site-packages (44.0.0)


In [2]:
neighborhoods2 = pd.read_csv(f"https://raw.githubusercontent.com/DirkFritz/Coursera_Capstone/master/Neighbourhoods.csv")
neighborhoods2 = neighborhoods2[["AREA_SHORT_CODE", "AREA_NAME", "LONGITUDE", "LATITUDE"]]
neighborhoods2=neighborhoods2.set_index("AREA_SHORT_CODE")

In [3]:
crimeData = pd.read_csv(f"https://raw.githubusercontent.com/DirkFritz/Coursera_Capstone/master/Neighbourhood_Crime_Rates_Boundary_File.csv")

In [4]:
neighborhoods2["Crime Rate"]= 0
for idx, row in crimeData.iterrows():
    hoodId = crimeData.loc[idx,"Hood_ID"]
    crimeRate = crimeData.loc[idx,"Assault_2018"] + crimeData.loc[idx,"Auto_Theft_2018"] + crimeData.loc[idx,"BreakandEnter_2018"] + crimeData.loc[idx,"Robbery_2018"] + crimeData.loc[idx,"Theft_Over_2018"] + crimeData.loc[idx,"Homicide_2018"]
    neighborhoods2.loc[hoodId,"Crime Rate"]=crimeRate


In [5]:
import urllib.request
from functools import partial 
torontoNeighBoundries = "https://raw.githubusercontent.com/DirkFritz/Coursera_Capstone/master/Neighbourhoods.geojson"

content=urllib.request.urlopen(torontoNeighBoundries)
    
gj = geojson.load(content)


neighborhoods2["Area m^2"]=0
for i in range(0,len(gj['features'])):           
    features = gj['features'][i]
    poly =features["geometry"]
    poly["type"]="Polygon"
    polygon = Polygon(poly['coordinates'][0])
    geom_area = transform(
    partial(
        pyproj.transform,
        pyproj.Proj(init='EPSG:4326'),
        pyproj.Proj(
            proj='aea',
            lat_1=polygon.bounds[3],
            lat_2=polygon.bounds[1])),
    polygon)
    hoodId= features["properties"]["AREA_SHORT_CODE"]
    neighborhoods2.loc[hoodId,"Area m^2"]=round(geom_area.area,0)
    

neighborhoods2=neighborhoods2.sort_values("AREA_NAME").reset_index()
#neighborhoods2

/opt/conda/envs/Python36/lib/python3.6/site-packages/pyproj/crs.py:77: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method.
  return _prepare_from_string(" ".join(pjargs))
/opt/conda/envs/Python36/lib/python3.6/site-packages/pyproj/crs.py:77: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method.
  return _prepare_from_string(" ".join(pjargs))
/opt/conda/envs/Python36/lib/python3.6/site-packages/pyproj/crs.py:77: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method.
  return _prepare_from_string(" ".join(pjargs))
/opt/conda/envs/Python36/lib/python3.6/site-packages/pyproj/crs.py:77: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method.
  return _prepare_from_string(" ".join(pjargs))
/opt/conda/envs/Python36

In [6]:
df_data_0 = pd.read_csv("https://raw.githubusercontent.com/DirkFritz/Coursera_Capstone/master/neighbourhood-profiles-2016-csv.csv")
population = df_data_0.iloc[2,:]
population=population.drop(["_id", "Category","Topic", "Data Source", "Characteristic", "City of Toronto"],axis=0)
#print(population)
neighborhoods2["Population"]=0
for idx, row in neighborhoods2.iterrows():
    neighborhoods2.loc[idx, "Population"]=int(population[idx].replace(",",""))

#neighborhoods2

In [7]:

latitude = 43.70460773398059
longitude = -79.39715291165048

map_toronto_crime= folium.Map(location=[latitude, longitude], zoom_start=11)
folium.Choropleth(
    geo_data=gj,  
    data=neighborhoods2,
    columns=['AREA_NAME', 'Crime Rate'],
    key_on='feature.properties.AREA_NAME',    
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Number of Crimes'  
    ).add_to(map_toronto_crime)


#map_toronto_crime


In [8]:

latitude = 43.70460773398059
longitude = -79.39715291165048

map_toronto_pop= folium.Map(location=[latitude, longitude], zoom_start=11)
folium.Choropleth(
    geo_data=gj,  
    data=neighborhoods2,
    columns=['AREA_NAME', 'Population'],
    key_on='feature.properties.AREA_NAME',    
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Population'  
    ).add_to(map_toronto_pop)

map_toronto_pop

In [9]:
neighborhoods2=neighborhoods2.fillna(0)
neighborhoods2.loc[:,"Person Per m^2"]= neighborhoods2["Population"]/neighborhoods2["Area m^2"]

In [10]:
longitude = -79.39715291165048

map_toronto_pop_dens= folium.Map(location=[latitude, longitude], zoom_start=11)
folium.Choropleth(
    geo_data=gj,  
    data=neighborhoods2,
    columns=['AREA_NAME', 'Person Per m^2'],
    key_on='feature.properties.AREA_NAME',    
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Population Density Persons per m^2'  
    ).add_to(map_toronto_pop_dens)

map_toronto_pop_dens

In [11]:
CLIENT_ID = "WKQBB1DZI22C3IPI4ADEQIKOA1PYAITSAN3NIY3VLMFTNSMG" # your Foursquare ID
CLIENT_SECRET = 'IMZYT4BECBUVICSHJJIHHY00F1I221IO3JOUCAF10RVHBWM3' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: WKQBB1DZI22C3IPI4ADEQIKOA1PYAITSAN3NIY3VLMFTNSMG
CLIENT_SECRET:IMZYT4BECBUVICSHJJIHHY00F1I221IO3JOUCAF10RVHBWM3


In [12]:
def getNearbyVenues(hoodId, names, latitudes, longitudes,categoryId, radius=500):
    
    venues_list=[]
    for hoodId, name, lat, lng in zip(hoodId, names, latitudes, longitudes):
        
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT, categoryId)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
       # print(results)
        # return only relevant information for each nearby venue
        venues_list.append([(
            hoodId,
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name'],
            v['venue']['categories'][0]['id']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['hoodId','Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category',
                  'Venue Id']
    
    return(nearby_venues)

In [13]:


LIMIT = 500 # limit of number of venues returned by Foursquare API
radius = 500 # define radius
#categoryId = "4d4b7105d754a06374d81259"
categoryId = "4bf58dd8d48988d1ca941735"

area_venues = getNearbyVenues(hoodId=neighborhoods2['AREA_SHORT_CODE'], names=neighborhoods2['AREA_NAME'],
                                   latitudes=neighborhoods2['LATITUDE'],
                                   longitudes=neighborhoods2['LONGITUDE'], categoryId=categoryId
                                  )
area_venues

hoodId                        Neighborhood  Neighborhood Latitude  \
0       129               Agincourt North (129)              43.805441   
1       128  Agincourt South-Malvern West (128)              43.788658   
2       128  Agincourt South-Malvern West (128)              43.788658   
3        20                      Alderwood (20)              43.604937   
4        20                      Alderwood (20)              43.604937   
5        95                          Annex (95)              43.671585   
6        95                          Annex (95)              43.671585   
7        42              Banbury-Don Mills (42)              43.737657   
8        42              Banbury-Don Mills (42)              43.737657   
9        42              Banbury-Don Mills (42)              43.737657   
10       76            Bay Street Corridor (76)              43.657511   
11       76            Bay Street Corridor (76)              43.657511   
12       76            Bay Street Corridor (76)              43.657511   
13       76            Bay Street Corridor (76)              43.657511   
14       76            Bay Street Corridor (76)              43.657511   
15       76            Bay Street Corridor (76)              43.657511   
16       76            Bay Street Corridor (76)              43.657511   
17       76            Bay Street Corridor (76)              43.657511   
18       76            Bay Street Corridor (76)              43.657511   
19       76            Bay Street Corridor (76)              43.657511   
20       76            Bay Street Corridor (76)              43.657511   
21       76            Bay Street Corridor (76)              43.657511   
22       76            Bay Street Corridor (76)              43.657511   
23       76            Bay Street Corridor (76)              43.657511   
24       76            Bay Street Corridor (76)              43.657511   
25       76            Bay Street Corridor (76)              43.657511   
26       76            Bay Street Corridor (76)              43.657511   
27       39           Bedford Park-Nortown (39)              43.731486   
28       39           Bedford Park-Nortown (39)              43.731486   
29       39           Bedford Park-Nortown (39)              43.731486   
..      ...                                 ...                    ...   
180      81              Trinity-Bellwoods (81)              43.650176   
181      81              Trinity-Bellwoods (81)              43.650176   
182      81              Trinity-Bellwoods (81)              43.650176   
183      81              Trinity-Bellwoods (81)              43.650176   
184      81              Trinity-Bellwoods (81)              43.650176   
185      79                     University (79)              43.662506   
186      79                     University (79)              43.662506   
187      79                     University (79)              43.662506   
188      43               Victoria Village (43)              43.728489   
189       1          West Humber-Clairville (1)              43.716180   
190       1          West Humber-Clairville (1)              43.716180   
191     113                        Weston (113)              43.702716   
192      91             Weston-Pellam Park (91)              43.673962   
193     119              Wexford/Maryvale (119)              43.748572   
194     119              Wexford/Maryvale (119)              43.748572   
195     100                Yonge-Eglinton (100)              43.704689   
196     100                Yonge-Eglinton (100)              43.704689   
197     100                Yonge-Eglinton (100)              43.704689   
198     100                Yonge-Eglinton (100)              43.704689   
199      97                 Yonge-St.Clair (97)              43.687859   
200      97                 Yonge-St.Clair (97)              43.687859   
201      97                 Yonge-St.Clair (97)              43.687859   
202      

In [14]:
# one hot encodin
area_onehot = pd.get_dummies(area_venues[['Venue Id']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
area_onehot["AREA_SHORT_CODE"]= ""
area_onehot["AREA_SHORT_CODE"] = area_venues["hoodId"] 

fixed_columns = [area_onehot.columns[-1]] + list(area_onehot.columns[:-1])
area_onehot = area_onehot[fixed_columns]

area_grouped = area_onehot.groupby('AREA_SHORT_CODE').mean().reset_index()
#area_grouped
area_grouped_sum = area_onehot.groupby('AREA_SHORT_CODE').sum().reset_index()
area_grouped = area_grouped.set_index('AREA_SHORT_CODE')
area_grouped_sum = area_grouped_sum.set_index('AREA_SHORT_CODE')
area_grouped_sum

4bf58dd8d48988d110941735  4bf58dd8d48988d116941735  \
AREA_SHORT_CODE                                                       
1                                       0                         0   
3                                       0                         0   
6                                       0                         0   
11                                      0                         0   
12                                      0                         0   
14                                      0                         0   
17                                      0                         0   
18                                      1                         0   
19                                      0                         0   
20                                      0                         0   
27                                      0                         0   
31                                      0                         0   
39                                      0                         0   
42                                      1                         0   
43                                      0                         0   
46                                      0                         0   
47                                      0                         0   
54                                      0                         0   
55                                      0                         0   
57                                      0                         0   
62                                      0                         0   
63                                      0                         0   
65                                      0                         0   
66                                      0                         0   
67                                      0                         0   
69                                      0                         0   
71                                      0                         0   
73                                      0                         0   
74                                      1                         0   
75                                      2                         0   
...                                   ...                       ...   
89                                      0                         0   
90                                      1                         0   
91                                      0                         0   
92                                      2                         0   
93                                      0                         1   
95                                      0                         0   
97                                      3                         0   
99                                      0                         0   
100                                     1                         0   
102                                     0                         0   
104                                     1                         0   
105                                     2                         0   
107                                     0                         0   
108                                     0                         0   
110                                     0                         0   
111                                     0                         0   
113                                     0                         0   
116                                     0                         0   
117                                     0                         0   
118                                     0                         0   
119                                     0                         0   
123                                     0                         0   
125                                     0                         0   
128                                     0

In [15]:
#neighborhoods2["Probability Venue"]=0
neighborhoods2["Sum Venue"]=0
neighborhoods2 = neighborhoods2.set_index('AREA_SHORT_CODE')

for hoodId, row in area_grouped.iterrows():
    #print(neighborhoods2.loc[hoodId, "AREA_NAME"] + str(area_grouped.loc[hoodId,"4bf58dd8d48988d1ca941735"]))
   # neighborhoods2.loc[hoodId, "Probability Venue"]=area_grouped.loc[hoodId,"4bf58dd8d48988d1ca941735"]
    neighborhoods2.loc[hoodId, "Sum Venue"]=area_grouped_sum.loc[hoodId,"4bf58dd8d48988d1ca941735"]
neighborhoods2.head(5)
#area_grouped

AREA_NAME  LONGITUDE   LATITUDE  \
AREA_SHORT_CODE                                                             
129                           Agincourt North (129) -79.266712  43.805441   
128              Agincourt South-Malvern West (128) -79.265612  43.788658   
20                                   Alderwood (20) -79.541611  43.604937   
95                                       Annex (95) -79.404001  43.671585   
42                           Banbury-Don Mills (42) -79.349718  43.737657   

                 Crime Rate    Area m^2  Population  Person Per m^2  Sum Venue  
AREA_SHORT_CODE                                                                 
129                   513.0   7264393.0       29113        0.004008          1  
128                   154.0   7875876.0       23757        0.003016          1  
20                    223.0   4980675.0       12054        0.002420          2  
95                    154.0   2791395.0       30526        0.010936          1  
42                     81.0  10045354.0       27695        0.002757          2

In [16]:
longitude = -79.39715291165048

map_toronto_venue= folium.Map(location=[latitude, longitude], zoom_start=11)
folium.Choropleth(
    geo_data=gj,  
    data=neighborhoods2,
    columns=['AREA_NAME', 'Sum Venue'],
    key_on='feature.properties.AREA_NAME',    
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Number of Venue Pizza Places'  
    ).add_to(map_toronto_venue)

map_toronto_venue